In [16]:
import chess.pgn
import pandas as pd
import chess
import numpy as np
from scipy import linalg

In [2]:
ls -shr

total 549M
6.4M  twic1417.pgn
6.8M  twic1417_moves.csv
 32K  twic1417_game_info.csv
4.5M  twic1407.pgn
 13M  twic1407_moves.csv
 72K  twic1407_game_info.csv
 16K  README.md
 89M  lichess_db_standard_rated_2013-01.pgn
286M  lichess_db_standard_rated_2013-01_moves.csv
 33M  lichess_db_standard_rated_2013-01_game_info.csv
568K  chess.ipynb
7.9M  chess-and-eigenvectors.ipynb
4.0K  caruana_carlsen_2018.pgn
160K  caruana_carlsen_2018_moves.csv
4.0K  caruana_carlsen_2018_game_info.csv
6.7M '2021-09.bare.[6516].pgn'
 43M '2021-09.bare.[6516]_moves.csv'
136K '2021-09.bare.[6516]_game_info.csv'
 11M '2021-01.bare.[10357].pgn'
 44M '2021-01.bare.[10357]_moves.csv'
152K '2021-01.bare.[10357]_game_info.csv'


In [3]:
board = chess.Board()

In [4]:
pgn = open('lichess_db_standard_rated_2013-01.pgn',encoding="utf-8")

In [5]:
#creates a list with one entry for each space on the board
spaces = []
for i in range(1,9):
    for j in range (1,9):
        spaces.append(chr(j+96)+str(i))

In [6]:
#create a matrix to tally weights for every pair of opposing pieces
pieces_list = [space for space in spaces if any(map(space.__contains__, ['1','2','7','8']))]
weights = pd.DataFrame(0,index=pieces_list, columns=pieces_list)

In [7]:
#create a state dictionary of each square and the initial square of each piece
#Those 'None' entries are the empty squares in the middle of the board, before the first move
#Each piece is on it's own square to begin
state_dict = {space:(space  if any(map(space.__contains__, ['1','2','7','8'])) else None) for space  in spaces}
state_dict

{'a1': 'a1',
 'b1': 'b1',
 'c1': 'c1',
 'd1': 'd1',
 'e1': 'e1',
 'f1': 'f1',
 'g1': 'g1',
 'h1': 'h1',
 'a2': 'a2',
 'b2': 'b2',
 'c2': 'c2',
 'd2': 'd2',
 'e2': 'e2',
 'f2': 'f2',
 'g2': 'g2',
 'h2': 'h2',
 'a3': None,
 'b3': None,
 'c3': None,
 'd3': None,
 'e3': None,
 'f3': None,
 'g3': None,
 'h3': None,
 'a4': None,
 'b4': None,
 'c4': None,
 'd4': None,
 'e4': None,
 'f4': None,
 'g4': None,
 'h4': None,
 'a5': None,
 'b5': None,
 'c5': None,
 'd5': None,
 'e5': None,
 'f5': None,
 'g5': None,
 'h5': None,
 'a6': None,
 'b6': None,
 'c6': None,
 'd6': None,
 'e6': None,
 'f6': None,
 'g6': None,
 'h6': None,
 'a7': 'a7',
 'b7': 'b7',
 'c7': 'c7',
 'd7': 'd7',
 'e7': 'e7',
 'f7': 'f7',
 'g7': 'g7',
 'h7': 'h7',
 'a8': 'a8',
 'b8': 'b8',
 'c8': 'c8',
 'd8': 'd8',
 'e8': 'e8',
 'f8': 'f8',
 'g8': 'g8',
 'h8': 'h8'}

In [8]:
game_counter = 0
game = chess.pgn.read_game(pgn)

while game is not None:
    counter = 0
    state_dict = {space:(space  if any(map(space.__contains__, ['1','2','7','8'])) else None) for space  in spaces}

    #print(game)
    #do stuff here



    #for each line in the file
    for move in game.mainline_moves():
        counter += 1
        if board.is_pseudo_legal(move):

            if board.is_checkmate():
                print("chekckmate")
                #do checkmate stuff here

            elif board.is_capture(move):
                capturing_piece = state_dict[chess.square_name(move.from_square)]
                captured_piece = state_dict[chess.square_name(move.to_square)]
                print('capturing piece',capturing_piece)
                print('captured piece',captured_piece)

                if board.is_en_passant(move):
                    #do en passant stuff here
                    print("en passant")
                elif capturing_piece is not None:
                    if captured_piece is not None:

                        #record the kill in a matrix of all kills
                        print(counter,chess.square_name(move.from_square), "takes on",chess.square_name(move.to_square))
                        print(counter,state_dict[chess.square_name(move.from_square)], "takes",state_dict[chess.square_name(move.to_square)])

                        #what piece is there now?
                     

                        #increment an entry in the weights matrix when one piece takes another
                        weights.loc[state_dict[chess.square_name(move.from_square)],state_dict[chess.square_name(move.to_square)]] += 1

                        #update the piece on the target square
                        state_dict[chess.square_name(move.to_square)] = state_dict[chess.square_name(move.from_square)]

                        #update the source square to be empty
                        state_dict[chess.square_name(move.from_square)] = None

                        #board.push(move)  # Make the move


                        #if df.loc[i+1,'move_no'] == 1:
                        #    state_dict = {space:(space  if any(map(space.__contains__, ['1','2','7','8'])) else None) for space  in spaces}
                else:
                    print("no legal moves")

            else:


                #add castling special cases to record both moves
                if board.is_kingside_castling(move):
                    if board.turn:
                        print(counter,'... and white castles kingside')
                        #move the appopriate rook
                        state_dict['f1'] = 'h1'
                        #leaving the rook source square empty
                        state_dict['h1'] = 'None'
                        #board.push(move)  # Make the move



                    elif not board.turn:
                        print(counter,'... and black castles kingside')
                        #move the appopriate rook
                        state_dict['f8'] = 'h8'
                        #leaving the rook source square empty
                        state_dict['h8'] = 'None'
                        #board.push(move)  # Make the move

                elif board.is_queenside_castling(move):
                    if board.turn:
                        print(counter,'... and white castles queenside')
                        #move the appopriate rook
                        state_dict['d1'] = 'a1'
                        #leaving the rook source square empty
                        state_dict['a1'] = 'None'
                        #board.push(move)  # Make the move

                    elif not board.turn:
                        print(counter,'... and black castles queenside')
                        #move the appopriate rook
                        state_dict['d8'] = 'a8'
                        #leaving the rook source square empty
                        state_dict['a8'] = 'None'
                        #board.push(move)  # Make the move

                else:
                    #update the piece on the target square
                    state_dict[chess.square_name(move.to_square)] = state_dict[chess.square_name(move.from_square)]

                    #update the source square to be empty
                    state_dict[chess.square_name(move.from_square)] = None


                    print(counter, chess.square_name(move.from_square),chess.square_name(move.to_square))

        board.push(move)  # Make the move
        #print(state_dict)

    game_counter += 1
    print('end of game',game_counter)
    print('board outcome',board.outcome())
    #print('chess outcome',chess.Outcome())
    print('is game over?',board.is_game_over())
    board.reset()

    game = chess.pgn.read_game(pgn)




    print(state_dict)

    

1 e2 e4
2 e7 e6
3 d2 d4
4 b7 b6
5 a2 a3
6 c8 b7
7 b1 c3
8 g8 h6
capturing piece c1
captured piece g8
9 c1 takes on h6
9 c1 takes g8
capturing piece g7
captured piece c1
10 g7 takes on h6
10 g7 takes c1
11 f1 e2
12 d8 g5
13 e2 g4
14 h6 h5
15 g1 f3
16 g5 g6
17 f3 h4
18 g6 g5
capturing piece f1
captured piece g7
19 g4 takes on h5
19 f1 takes g7
capturing piece d8
captured piece g1
20 g5 takes on h4
20 d8 takes g1
21 d1 f3
22 e8 d8
capturing piece d1
captured piece f7
23 f3 takes on f7
23 d1 takes f7
24 b8 c6
25 f7 e8
end of game 1
board outcome Outcome(termination=<Termination.CHECKMATE: 1>, winner=True)
is game over? True
{'a1': 'a1', 'b1': None, 'c1': None, 'd1': None, 'e1': 'e1', 'f1': None, 'g1': None, 'h1': 'h1', 'a2': None, 'b2': 'b2', 'c2': 'c2', 'd2': None, 'e2': None, 'f2': 'f2', 'g2': 'g2', 'h2': 'h2', 'a3': 'a2', 'b3': None, 'c3': 'b1', 'd3': None, 'e3': None, 'f3': None, 'g3': None, 'h3': None, 'a4': None, 'b4': None, 'c4': None, 'd4': 'd2', 'e4': 'e2', 'f4': None, 'g4': None,

captured piece g8
27 g5 takes on e6
27 g1 takes g8
capturing piece c8
captured piece g1
28 d7 takes on e6
28 c8 takes g1
29 c3 d5
30 h5 h4
31 h2 h3
capturing piece c8
captured piece h2
32 e6 takes on h3
32 c8 takes h2
capturing piece g2
captured piece c8
33 g2 takes on h3
33 g2 takes c8
34 d8 g5
35 g1 f1
36 b8 d7
37 d1 a4
38 d7 f6
39 d5 e7
40 g8 h8
41 f2 f3
42 g5 g3
43 f1 e2
capturing piece d8
captured piece g2
44 g3 takes on h3
44 d8 takes g2
45 e1 h1
46 h3 g2
47 e2 e3
48 h4 h3
49 a4 d1
50 a8 e8
51 d3 f1
52 f6 g4
53 e3 d3
54 g4 e5
55 d3 c3
56 g2 g3
capturing piece h1
captured piece h7
57 h1 takes on h3
57 h1 takes h7
capturing piece d8
captured piece h1
58 g3 takes on h3
58 d8 takes h1
capturing piece f1
captured piece d8
59 f1 takes on h3
59 f1 takes d8
capturing piece a8
captured piece b1
60 e8 takes on e7
60 a8 takes b1
capturing piece d1
captured piece d7
61 d1 takes on d6
61 d1 takes d7
62 e5 c6
63 a1 h1
64 f8 d8
capturing piece d1
captured piece c7
65 d6 takes on c5
65 d1 takes 

{'a1': None, 'b1': None, 'c1': None, 'd1': None, 'e1': 'e1', 'f1': 'h8', 'g1': None, 'h1': 'None', 'a2': 'a2', 'b2': 'b2', 'c2': None, 'd2': None, 'e2': None, 'f2': None, 'g2': None, 'h2': 'h2', 'a3': None, 'b3': 'f1', 'c3': None, 'd3': 'd2', 'e3': None, 'f3': None, 'g3': None, 'h3': None, 'a4': None, 'b4': 'b7', 'c4': None, 'd4': 'c1', 'e4': None, 'f4': None, 'g4': None, 'h4': None, 'a5': 'a7', 'b5': None, 'c5': None, 'd5': None, 'e5': None, 'f5': None, 'g5': None, 'h5': 'h7', 'a6': None, 'b6': None, 'c6': None, 'd6': None, 'e6': None, 'f6': None, 'g6': 'd1', 'h6': 'e8', 'a7': None, 'b7': None, 'c7': None, 'd7': None, 'e7': None, 'f7': None, 'g7': None, 'h7': None, 'a8': None, 'b8': None, 'c8': None, 'd8': 'f8', 'e8': None, 'f8': None, 'g8': 'f2', 'h8': None}
1 e2 e4
2 c7 c5
3 f2 f4
4 d7 d5
capturing piece e2
captured piece d7
5 e4 takes on d5
5 e2 takes d7
capturing piece d8
captured piece e2
6 d8 takes on d5
6 d8 takes e2
7 b1 c3
8 d5 d8
9 f1 c4
10 c8 f5
11 d2 d3
12 a7 a6
13 g2 g4
1

24 f7 e8
25 ... and white castles kingside
26 d7 d5
27 f1 e1
28 e8 d8
29 c1 g5
30 d8 c7
31 c4 b3
32 b8 d7
33 c3 c4
34 g8 f6
35 g5 f4
36 c7 b7
capturing piece c2
captured piece d7
37 c4 takes on d5
37 c2 takes d7
capturing piece g8
captured piece c2
38 f6 takes on d5
38 g8 takes c2
capturing piece f1
captured piece g8
39 b3 takes on d5
39 f1 takes g8
capturing piece c7
captured piece f1
40 c6 takes on d5
40 c7 takes f1
41 b1 c3
42 d7 f6
43 a2 a4
44 c8 d7
45 a4 a5
46 b6 b5
47 a5 a6
48 b7 c6
49 f4 e5
50 a8 e8
51 f2 f4
52 e8 e6
53 e1 c1
54 c6 b6
55 e5 d4
56 b6 c7
capturing piece b1
captured piece b7
57 c3 takes on b5
57 b1 takes b7
58 c7 b8
59 b5 c7
60 e6 c6
capturing piece h1
captured piece a8
61 c1 takes on c6
61 h1 takes a8
capturing piece c8
captured piece h1
62 d7 takes on c6
62 c8 takes h1
capturing piece c1
captured piece b8
63 d4 takes on f6
63 c1 takes b8
capturing piece e8
captured piece b1
64 b8 takes on c7
64 e8 takes b1
capturing piece c1
captured piece g7
65 f6 takes on g7
65

90 a2 c1
91 f8 f7
92 h7 h8
93 e5 e6
end of game 24
board outcome None
is game over? False
{'a1': None, 'b1': None, 'c1': 'b8', 'd1': None, 'e1': None, 'f1': None, 'g1': None, 'h1': None, 'a2': None, 'b2': None, 'c2': None, 'd2': None, 'e2': None, 'f2': None, 'g2': 'g2', 'h2': None, 'a3': None, 'b3': 'b2', 'c3': None, 'd3': None, 'e3': None, 'f3': None, 'g3': None, 'h3': 'h2', 'a4': 'a2', 'b4': 'b7', 'c4': None, 'd4': None, 'e4': None, 'f4': None, 'g4': None, 'h4': None, 'a5': 'a7', 'b5': None, 'c5': None, 'd5': None, 'e5': None, 'f5': None, 'g5': None, 'h5': None, 'a6': None, 'b6': None, 'c6': None, 'd6': None, 'e6': 'd2', 'f6': None, 'g6': None, 'h6': 'h7', 'a7': None, 'b7': None, 'c7': None, 'd7': None, 'e7': None, 'f7': 'd1', 'g7': None, 'h7': None, 'a8': None, 'b8': None, 'c8': None, 'd8': None, 'e8': None, 'f8': None, 'g8': None, 'h8': None}
1 e2 e4
2 e7 e5
3 g1 f3
4 d8 f6
5 d2 d4
6 d7 d6
7 d4 d5
8 c8 d7
9 b1 c3
10 a7 a6
11 c1 e3
12 f8 e7
13 d1 d3
14 g8 h6
15 d3 c4
16 e7 d8
17 ...

...

73 f1 g1
capturing piece h8
captured piece b2
74 f3 takes on b3
74 h8 takes b2
75 e1 f1
76 e6 e5
77 a6 b5
78 b3 b2
79 f1 e1
80 c2 h2
81 b5 c6
82 b2 g2
83 g1 f1
84 g2 d2
85 f1 g1
86 h2 e2
capturing piece a1
captured piece a8
87 e1 takes on e2
87 a1 takes a8
capturing piece h8
captured piece a1
88 d2 takes on e2
88 h8 takes a1
capturing piece f1
captured piece d7
89 c6 takes on d5
89 f1 takes d7
90 e2 d2
91 d5 c6
92 g7 f6
93 g1 f1
94 f6 f5
95 f1 e1
96 d2 b2
97 e1 d1
98 f5 f4
99 d1 c1
100 b2 h2
101 c1 d1
102 f4 e3
103 d1 e1
104 h2 a2
105 e1 d1
106 e5 e4
107 d1 c1
108 a2 h2
109 c1 b1
110 e3 d3
111 c6 b5
112 d3 c3
end of game 1714
board outcome None
is game over? False
{'a1': None, 'b1': 'g8', 'c1': None, 'd1': None, 'e1': None, 'f1': None, 'g1': None, 'h1': None, 'a2': None, 'b2': None, 'c2': None, 'd2': None, 'e2': None, 'f2': None, 'g2': None, 'h2': 'h8', 'a3': None, 'b3': None, 'c3': 'c1', 'd3': None, 'e3': None, 'f3': None, 'g3': None, 'h3': None, 'a4': 'a2', 'b4': None, 'c4': None, 'd

71 g1 takes c7
capturing piece h8
captured piece h2
72 e2 takes on h2
72 h8 takes h2
end of game 1720
board outcome Outcome(termination=<Termination.CHECKMATE: 1>, winner=False)
is game over? True
{'a1': None, 'b1': None, 'c1': 'a1', 'd1': None, 'e1': 'e1', 'f1': None, 'g1': None, 'h1': None, 'a2': None, 'b2': None, 'c2': None, 'd2': 'a8', 'e2': None, 'f2': None, 'g2': None, 'h2': 'h8', 'a3': None, 'b3': None, 'c3': None, 'd3': None, 'e3': None, 'f3': None, 'g3': None, 'h3': None, 'a4': 'a2', 'b4': None, 'c4': None, 'd4': None, 'e4': None, 'f4': 'g2', 'g4': 'g7', 'h4': 'h7', 'a5': 'a7', 'b5': 'b2', 'c5': None, 'd5': None, 'e5': None, 'f5': None, 'g5': None, 'h5': None, 'a6': None, 'b6': 'f8', 'c6': 'h1', 'd6': None, 'e6': None, 'f6': 'f7', 'g6': None, 'h6': None, 'a7': None, 'b7': None, 'c7': 'g1', 'd7': None, 'e7': None, 'f7': None, 'g7': None, 'h7': None, 'a8': 'None', 'b8': None, 'c8': None, 'd8': None, 'e8': None, 'f8': None, 'g8': None, 'h8': None}
1 e2 e4
2 e7 e5
3 g1 f3
4 b8 c6


46 d8 takes c1
47 a6 c4
48 f8 f7
49 g1 f1
50 c6 f3
51 d1 c1
52 f2 d2
53 c1 b1
54 f3 e4
55 c4 c2
capturing piece d8
captured piece d1
56 d2 takes on c2
56 d8 takes d1
end of game 1725
board outcome Outcome(termination=<Termination.CHECKMATE: 1>, winner=False)
is game over? True
{'a1': 'a1', 'b1': 'e1', 'c1': None, 'd1': None, 'e1': None, 'f1': 'h1', 'g1': None, 'h1': None, 'a2': 'a2', 'b2': 'b2', 'c2': 'd8', 'd2': None, 'e2': None, 'f2': None, 'g2': None, 'h2': 'h2', 'a3': None, 'b3': None, 'c3': None, 'd3': None, 'e3': None, 'f3': None, 'g3': None, 'h3': None, 'a4': None, 'b4': 'f8', 'c4': None, 'd4': None, 'e4': 'c8', 'f4': None, 'g4': None, 'h4': None, 'a5': None, 'b5': None, 'c5': None, 'd5': None, 'e5': 'e7', 'f5': None, 'g5': None, 'h5': None, 'a6': None, 'b6': 'b7', 'c6': None, 'd6': None, 'e6': None, 'f6': None, 'g6': 'g7', 'h6': None, 'a7': None, 'b7': None, 'c7': None, 'd7': 'b8', 'e7': None, 'f7': 'h8', 'g7': None, 'h7': 'h7', 'a8': None, 'b8': None, 'c8': 'a8', 'd8': None, '

17 h2 h3
18 d6 g6
19 g2 g3
20 h7 h5
capturing piece b1
captured piece d7
21 d2 takes on c4
21 b1 takes d7
22 e7 e6
23 c4 e5
24 g6 f6
25 h3 h4
26 f8 d6
27 e5 f3
28 g8 h6
29 c3 c4
30 c7 c5
31 b4 b5
capturing piece c7
captured piece d2
32 c5 takes on d4
32 c7 takes d2
capturing piece b1
captured piece c7
33 f3 takes on d4
33 b1 takes c7
34 f5 g4
35 d1 d2
36 d6 c5
37 c1 b2
capturing piece f8
captured piece b1
38 c5 takes on d4
38 f8 takes b1
capturing piece c1
captured piece f8
39 b2 takes on d4
39 c1 takes f8
capturing piece a8
captured piece c1
40 d8 takes on d4
40 a8 takes c1
capturing piece d1
captured piece a8
41 d2 takes on d4
41 d1 takes a8
42 h8 d8
capturing piece d1
captured piece a7
43 d4 takes on a7
43 d1 takes a7
capturing piece d8
captured piece a1
44 f6 takes on a1
44 d8 takes a1
end of game 1729
board outcome Outcome(termination=<Termination.CHECKMATE: 1>, winner=False)
is game over? True
{'a1': 'd8', 'b1': None, 'c1': None, 'd1': None, 'e1': 'e1', 'f1': None, 'g1': 'g1', 'h

KeyboardInterrupt: 

In [9]:
weights

a1   b1   c1   d1  e1   f1   g1   h1  a2   b2  ...  g7  h7   a8   b8  \
a1    0    0    2    0   0    0    1    3   4    0  ...  35  27  159   51   
b1    1    0    1    0   0    0    1    1   2    1  ...  30  17   56   62   
c1    1    2    0    1   0    0    1    0   2    1  ...  58  56   35  126   
d1    2    1    0    0   0    2    1    1   2    1  ...  87  99  127  182   
e1    0    0    0    0   0    0    0    0   0    0  ...   7  15   10   15   
f1    1    0    1    1   0    0    0    1   0    0  ...  26  44   64  253   
g1    2    0    3    0   0    0    0    0   1    1  ...  38  36   28  217   
h1    0    1    1    1   0    0    1    0   3    3  ...  48  47  123   49   
a2    0    0    0    0   0    0    1    0   0    2  ...   1   3    6   18   
b2    1    1    1    0   0    0    0    0   0    0  ...   1   0    7   25   
c2    0    0    0    0   0    0    0    0   1    1  ...   1   2    6   36   
d2    0    0    0    0   0    0    0    0   1    1  ...   4   1    6   51   
e2    0    0    0    0   0    0    1    0   0    1  ...  16   2    4   19   
f2    0    0    0    0   0    0    2    0   0    0  ...  62  17    7   27   
g2    1    0    0    0   0    0    0    2   1    0  ...  38  32    4   22   
h2    2    0    1    0   0    1    0    0   1    1  ...  77  45    1    9   
a7    2   21   21    7   0   10    4    2  51   89  ...   0   0    0    0   
b7    8   11   12    6   0  118   43    4  57   49  ...   1   2    0    0   
c7    8   31   28    8   0   31   26    2  23   53  ...   1   2    0    0   
d7    3   40   13   11   0   45   34    7   2   25  ...   0   1    0    1   
e7    1   30   28   13   0   33   47    4   1    8  ...   1   2    0    0   
f7    2   20   14   16   0   59   48    6   0    0  ...   4   4    1    0   
g7    4   24   69   16   0    8   20    9   1    0  ...   0   2    2    0   
h7    3    3   16    9   0   23   30    8   2    1  ...   2   0    0    0   
a8  190   70   75   68   0   60   40  117  74   64  ...   7   4    0    0   
b8   42   74   88   45   0  157  191   46  23   51  ...   1   0    4    0   
c8   43  130    0   53   0  262  265   67  30   19  ...   1   0    2    0   
d8  111  147  207  353   0  133  147  106  72  132  ...   2   1    2    3   
e8   20   22   34   47   0   35   20   15  11    9  ...   0   0    0    0   
f8   70  235  284   60   0    0  152   57  27   86  ...   2   0    2    1   
g8   21  195  133   55   0  100   91   52  16   29  ...   1   1    2    0   
h8  125   58   72   66   0   53   71  160  56   43  ...   2   7    0    0   

     c8   d8  e8   f8   g8   h8  
a1   57   75   0   57   44  139  
b1   73   65   0  128  188   42  
c1    0   52   0  288  283   76  
d1  219  366   0  170  160  117  
e1   18   36   0   25   21   16  
f1  307   49   0    0  140   43  
g1  115   66   0   92   85   46  
h1   79   78   0   78   52  145  
a2   14    5   0   10    4    4  
b2    5    9   0   94   36    1  
c2   17    7   0   19   19    1  
d2   23    4   0   40   36    2  
e2   40   17   0   27   51    4  
f2   20   10   0   37   53    7  
g2   80   13   0   17   20   10  
h2   10   11   0   14   32    6  
a7    0    0   0    0    0    0  
b7    0    0   0    0    0    1  
c7    0    0   0    1    0    1  
d7    0    0   0    0    0    0  
e7    0    0   0    0    0    1  
f7    0    0   0    0    0    1  
g7    2    0   0    0    1    0  
h7    2    0   0    0    0    0  
a8    1    0   0    0    1    6  
b8    0    0   0    0    1    1  
c8    0    3   0    0    2    3  
d8    2    0   0    1    1    1  
e8    0    0   0    0    0    0  
f8    0    0   0    0    0    0  
g8    0    1   0    0    0    1  
h8    2    1   0    1    1    0  

[32 rows x 32 columns]

In [ ]:
dict_of_games = {}
counter = 0
while counter < 1000:
    game = chess.pgn.read_game(pgn)
    dict_of_games[str(counter)] = game
    counter += 1
    if game is None:
        break

In [ ]:
dict_of_games

In [ ]:
counter = 0
while counter < 10:
    game = chess.pgn.read_game(pgn)
    if game is None:
        break
    #do stuff here
    for move in game.mainline_moves():
        print(move.uci())
    counter += 1
    print('end of game',counter)


In [ ]:
game

In [ ]:
move

In [ ]:
move.drop

In [ ]:
move.from_square
chess.square_name(move.from_square)

In [ ]:
board = chess.Board()
board.is_attacked_by(chess.WHITE, chess.E3)

In [ ]:
board.reset()
game = chess.pgn.read_game(pgn)

for move in game.mainline_moves():
        print(move.uci())
        print('turn?' , board.turn)
        print('is game over?' , board.is_game_over())
        print('from square: ' ,chess.square_name(move.from_square))
        print('to square: ' ,chess.square_name(move.to_square))
        print('drop: ' ,move.drop)
        print('is capture?' , board.is_capture(move))
        print('is en passant capture?' , board.is_en_passant(move))
        print('is kingside castle?' , board.is_kingside_castling(move))
        print('is quenside castle?' , board.is_queenside_castling(move))

        board.push(move)  # Make the move
        print('is_checkmate?' , board.is_checkmate())
        #print('checkers' , board.checkers())
        print('outcome' , board.outcome())

        #print(board)
        #print(board.piece_map())
    #board

In [ ]:
board.reset()
print(game.mainline_moves)
board

In [ ]:
#piece.piece_type()

In [ ]:
board.reset()
dict = board.piece_map()
dict

In [ ]:
dict[0]

In [ ]:
#weights.drop(columns=['e1', 'e8'],inplace=True)
#weights.drop(index=['e1', 'e8'],inplace=True)

In [13]:
a = weights - np.identity(32)
print(a)

       a1     b1     c1     d1   e1     f1     g1     h1    a2     b2  ...  \
a1   -1.0    0.0    2.0    0.0  0.0    0.0    1.0    3.0   4.0    0.0  ...   
b1    1.0   -1.0    1.0    0.0  0.0    0.0    1.0    1.0   2.0    1.0  ...   
c1    1.0    2.0   -1.0    1.0  0.0    0.0    1.0    0.0   2.0    1.0  ...   
d1    2.0    1.0    0.0   -1.0  0.0    2.0    1.0    1.0   2.0    1.0  ...   
e1    0.0    0.0    0.0    0.0 -1.0    0.0    0.0    0.0   0.0    0.0  ...   
f1    1.0    0.0    1.0    1.0  0.0   -1.0    0.0    1.0   0.0    0.0  ...   
g1    2.0    0.0    3.0    0.0  0.0    0.0   -1.0    0.0   1.0    1.0  ...   
h1    0.0    1.0    1.0    1.0  0.0    0.0    1.0   -1.0   3.0    3.0  ...   
a2    0.0    0.0    0.0    0.0  0.0    0.0    1.0    0.0  -1.0    2.0  ...   
b2    1.0    1.0    1.0    0.0  0.0    0.0    0.0    0.0   0.0   -1.0  ...   
c2    0.0    0.0    0.0    0.0  0.0    0.0    0.0    0.0   1.0    1.0  ...   
d2    0.0    0.0    0.0    0.0  0.0    0.0    0.0    0.0   1.0  

In [14]:
b = np.zeros(32)
print(b)

[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]


In [17]:
x = linalg.solve(a, b)
x

array([ 0.,  0., -0.,  0., -0.,  0., -0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0., -0.,  0., -0., -0.,  0.,
       -0., -0., -0.,  0., -0.,  0.])

### Why doesn't it work?
### Because the solver is finding the trivial solution. i.e. just a vector full of zeroes.
### To check that there is actually a non trivial solution, the determinant of A must be non-zero.

In [18]:
np.linalg.det(a)

5.356763127911189e+58

### OK since the determinant is not zero, there must be at least one non-trivial solution. How to find it?
### An homogenous linear equation can be solved with a Matrix Factorization.

In [19]:
eigen_values, eigen_vectors = np.linalg.eig(a)  

In [20]:
values = eigen_vectors[:, np.argmin(eigen_values)] 

In [21]:
## Let's normalize the values

In [28]:
list = []
for i in values:
    list.append(abs(float(i)))

<ipython-input-28-fd238d3eb4fa>:3: ComplexWarning: Casting complex values to real discards the imaginary part
  list.append(abs(float(i)))


In [29]:
#The fractional inverse of the strongest pawn
factor = 1 / np.max(list[8:-8])

In [30]:
normed = [i*factor for i in list]

In [31]:
normalized_list = ["%.2f"%i for i in normed]

In [32]:
print(normalized_list[0:8])
print(normalized_list[8:8+8])
print(normalized_list[8+8:8+8+8])
print(normalized_list[-8:])

['1.90', '2.18', '2.72', '5.28', '0.53', '2.78', '2.32', '2.00']
['0.31', '0.67', '0.67', '0.85', '1.00', '0.67', '0.58', '0.33']
['0.32', '0.76', '0.83', '0.86', '0.96', '0.73', '0.55', '0.37']
['1.95', '2.23', '2.57', '4.99', '0.74', '2.79', '2.28', '1.95']
